# ML Pipeline Preparation
Follow the instructions below to help you create your ML pipeline.
### 1. Import libraries and load data from database.
- Import Python libraries
- Load dataset from database with [`read_sql_table`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_sql_table.html)
- Define feature and target variables X and Y

In [2]:
# import libraries
import pandas as pd

In [3]:
# load data from database
from sqlalchemy import create_engine

engine = create_engine('sqlite:///disasterResponse.db')
df = pd.read_sql("SELECT * FROM disasterResponse", engine)
X = df['message']
y = df.drop(['id', 'message', 'original', 'genre'], axis = 1)

### 2. Write a tokenization function to process your text data

In [4]:
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet') 

from nltk import word_tokenize
import re
from nltk.stem.wordnet import WordNetLemmatizer

from nltk.corpus import stopwords

def tokenize(text):
    # normalized
    text = text.lower()
    # remove punctuation
    text = re.sub(r'[^a-z0-9\s]+', '', text)
    # split on space    
    words = word_tokenize(text)
    # remove stop words    
    words = [w for w in words if w not in stopwords.words("english")]
    # lemmatize 
    lemmed = [WordNetLemmatizer().lemmatize(w, pos='v') for w in words]
    
    return lemmed

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


In [5]:
# Test tokenization
for s in X.unique():
    print("***", s)
    print("---",tokenize(s))

*** Weather update - a cold front from Cuba that could pass over Haiti
--- ['weather', 'update', 'cold', 'front', 'cuba', 'could', 'pass', 'haiti']
*** Is the Hurricane over or is it not over
--- ['hurricane']
*** Looking for someone but no name
--- ['look', 'someone', 'name']
*** UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs supplies desperately.
--- ['un', 'report', 'leogane', '8090', 'destroy', 'hospital', 'st', 'croix', 'function', 'need', 'supply', 'desperately']
*** says: west side of Haiti, rest of the country today and tonight
--- ['say', 'west', 'side', 'haiti', 'rest', 'country', 'today', 'tonight']
*** Information about the National Palace-
--- ['information', 'national', 'palace']
*** Storm at sacred heart of jesus
--- ['storm', 'sacred', 'heart', 'jesus']
*** Please, we need tents and water. We are in Silo, Thank you!
--- ['please', 'need', 'tent', 'water', 'silo', 'thank']
*** I would like to receive the messages, thank you
--- ['would', '

### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [6]:
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.model_selection import train_test_split
from sklearn.multioutput import MultiOutputClassifier


pipeline = Pipeline([
    ('vect', CountVectorizer(tokenizer = tokenize)),
    ('tfidf', TfidfTransformer()),
    ('clf', MultiOutputClassifier(RandomForestClassifier()))
])

np.unique(X)

array(['    ', '                           ', '          .', ...,
       "zone ''salo'' near in the common ''Verettes 4th section ",
       "zone in hunger their killing us in zone, we can't. ..",
       '| News Update | Serious loss of life expected in devastating earthquake in Haiti http ow.ly 16klRU'], dtype=object)

### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [7]:
X_train, X_test, y_train, y_test = train_test_split(X, y)

pipeline.fit(X_train, y_train)

Pipeline(memory=None,
     steps=[('vect', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), preprocessor=None, stop_words=None,
        strip...oob_score=False, random_state=None, verbose=0,
            warm_start=False),
           n_jobs=1))])

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

In [8]:
def get_eval_metrics(actual, predicted, col_names):
    """Calculate evaluation metrics for ML model
    
    Args:
    actual: array. Array containing actual labels.
    predicted: array. Array containing predicted labels.
    col_names: list of strings. List containing names for each of the predicted fields.
       
    Returns:
    metrics_df: dataframe. Dataframe containing the accuracy, precision, recall 
    and f1 score for a given set of actual and predicted labels.
    """
    metrics = []
    
    # Calculate evaluation metrics for each set of labels
    for i in range(len(col_names)):
        accuracy = accuracy_score(actual[:, i], predicted[:, i])
        precision = precision_score(actual[:, i], predicted[:, i])
        recall = recall_score(actual[:, i], predicted[:, i])
        f1 = f1_score(actual[:, i], predicted[:, i])
        
        metrics.append([accuracy, precision, recall, f1])
    
    # Create dataframe containing metrics
    metrics = np.array(metrics)
    metrics_df = pd.DataFrame(data = metrics, index = col_names, columns = ['Accuracy', 'Precision', 'Recall', 'F1'])
      
    return metrics_df

from sklearn.metrics import classification_report
y_pred = pipeline.predict(X_test)

In [9]:
# Get results and add them to a dataframe.
def get_classification_report(y_test, y_pred):
    """
    To get F1 score,precision for each category
    Param:
    y_test - actual y values 
    y_pred - predicted y values
    """
    for ind,cat in enumerate(y_test.keys()): 
        print("Classification report for {}".format(cat))
        print(classification_report(y_test.iloc[:,ind], y_pred[:,ind]))
        
print(get_classification_report(y_test, y_pred))    

Classification report for related
             precision    recall  f1-score   support

          0       0.61      0.43      0.50      1565
          1       0.83      0.91      0.87      4948
          2       0.22      0.32      0.26        41

avg / total       0.78      0.79      0.78      6554

Classification report for request
             precision    recall  f1-score   support

          0       0.89      0.98      0.93      5433
          1       0.79      0.43      0.56      1121

avg / total       0.87      0.88      0.87      6554

Classification report for offer
             precision    recall  f1-score   support

          0       1.00      1.00      1.00      6525
          1       0.00      0.00      0.00        29

avg / total       0.99      1.00      0.99      6554

Classification report for aid_related
             precision    recall  f1-score   support

          0       0.76      0.85      0.80      3840
          1       0.75      0.61      0.67      2714

avg

/opt/conda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


### 6. Improve your model
Use grid search to find better parameters. 

In [10]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, make_scorer

# Define performance metric for use in grid search scoring object
def performance_metric(y_true, y_pred):
    """Calculate median F1 score for all of the output classifiers
    
    Args:
    y_true: array. Array containing actual labels.
    y_pred: array. Array containing predicted labels.
        
    Returns:
    score: float. Median F1 score for all of the output classifiers
    """
    f1_list = []
    for i in range(np.shape(y_pred)[1]):
        f1 = f1_score(np.array(y_true)[:, i], y_pred[:, i])
        f1_list.append(f1)
        
    score = np.median(f1_list)
    return score

In [11]:
from sklearn.model_selection import GridSearchCV
import numpy as np

parameters = {
    'vect__min_df': [1, 5]
}

scorer = make_scorer(performance_metric)
#cv = GridSearchCV(pipeline, param_grid=parameters, scoring = scorer)
cv = GridSearchCV(pipeline, param_grid=parameters)

# Find best parameters
tuned_model = cv.fit(X_train, y_train)

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

In [12]:
tuned_model.predict(X_test)
print(get_classification_report(y_test, y_pred))    

Classification report for related
             precision    recall  f1-score   support

          0       0.61      0.43      0.50      1565
          1       0.83      0.91      0.87      4948
          2       0.22      0.32      0.26        41

avg / total       0.78      0.79      0.78      6554

Classification report for request
             precision    recall  f1-score   support

          0       0.89      0.98      0.93      5433
          1       0.79      0.43      0.56      1121

avg / total       0.87      0.88      0.87      6554

Classification report for offer
             precision    recall  f1-score   support

          0       1.00      1.00      1.00      6525
          1       0.00      0.00      0.00        29

avg / total       0.99      1.00      0.99      6554

Classification report for aid_related
             precision    recall  f1-score   support

          0       0.76      0.85      0.80      3840
          1       0.75      0.61      0.67      2714

avg

/opt/conda/lib/python3.6/site-packages/sklearn/metrics/classification.py:1135: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

In [13]:
# Try using SVM instead of Random Forest Classifier
from sklearn.svm import SVC

pipeline2 = Pipeline([
    ('vect', CountVectorizer(tokenizer = tokenize)),
    ('tfidf', TfidfTransformer()),
    ('clf', MultiOutputClassifier(SVC()))
])

parameters2 = {
    'vect__min_df': [1, 5]
}

#cv2 = GridSearchCV(pipeline2, param_grid = parameters2, scoring = scorer, verbose = 10)
cv2 = GridSearchCV(pipeline2, param_grid = parameters2, verbose = 10)

# Find best parameters
tuned_model2 = cv2.fit(X_train, y_train)

Fitting 3 folds for each of 2 candidates, totalling 6 fits
[CV] vect__min_df=1 ..................................................


ValueError: The number of classes has to be greater than one; got 1

In [ ]:
# Get results of grid search
tuned_model2.cv_results_

In [ ]:
# Calculate evaluation metrics for test set
tuned_pred_test2 = tuned_model2.predict(X_test)

eval_metrics2 = get_eval_metrics(np.array(Y_test), tuned_pred_test2, col_names)

print(eval_metrics2)

### 9. Export your model as a pickle file

In [ ]:
# Pickle best model
import pickle

pickle.dump(tuned_model, open('disaster_model.sav', 'wb'))

### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.